In [18]:
import __init__
#
from taxi_common.file_handling_functions import load_pickle_file
from taxi_common.sg_grid_zone import get_sg_grid_xy_points, get_sg_zones
#
from IPython.display import HTML, display
import folium

from community_analysis import dpaths, prefixs
import pandas as pd
from taxi_common import sg_grid_geojson

In [19]:
def draw_interesting_zones(df, zizj_weight, withHeatMap = False):
    x_points, y_points = get_sg_grid_xy_points()
    xc, yc = (x_points[0] + x_points[-1]) / float(2), (y_points[0] + y_points[-1]) / float(2)
    color_map = ['red', 'green', 'blue', 'orange', 'black', 'purple', 'gray', 'white']
    #
    map_osm = folium.Map(location=[yc, xc], zoom_start=11)
    for x in x_points:
        sx, sy, ex, ey = x, y_points[0], x, y_points[-1]
        map_osm.add_children(folium.PolyLine(locations=[(sy, sx), (ey, ex)], weight=1.0))
    for y in y_points:
        sx, sy, ex, ey = x_points[0], y, x_points[-1], y
        map_osm.add_children(folium.PolyLine(locations=[(sy, sx), (ey, ex)], weight=1.0))
    #
    zones = get_sg_zones()
    allZones = set(['%d#%d' % (zi, zj) for zi, zj in zones.iterkeys()])
    tripOccuredZones = set(df['zizj'])
    zizj_tripNum_df = df.groupby(['zizj']).count()['did'].to_frame('numTrips').reset_index()
    if withHeatMap:
        noneTripZones = allZones.difference(tripOccuredZones)
        for zizj in noneTripZones:
            zizj_tripNum_df.loc[-1] = [zizj, 0]
            zizj_tripNum_df.index = zizj_tripNum_df.index + 1
        map_osm.geo_json(geo_path=sg_grid_geojson, data=zizj_tripNum_df,
                    columns=['zizj', 'numTrips'],
                    key_on='feature.id',
                    fill_color='BuPu', fill_opacity=0.55, line_opacity=0.2)
    ranks = []
    num_allZones = len(tripOccuredZones)
    for j, (zizj, _) in enumerate(zizj_tripNum_df.sort_values(by='numTrips', ascending=False).values):
        zi, zj = map(int, zizj.split('#'))
        y, x = zones[(zi, zj)].cCoor_gps
        if zizj in zizj_weight.keys():
            text = '%s %.2f, %d, %d' % (zizj, zizj_weight[zizj], j, num_allZones)
            ranks.append((j, text))
            folium.Marker((y, x),
                              popup='%d (%d#%d)' % (j, zi, zj),
                          icon=folium.Icon(color=color_map[0])
                          ).add_to(map_osm)
    for _, x in sorted(ranks):
        print x
    return map_osm

In [20]:
def draw_interesting_zones_byNumVisit(df):
    x_points, y_points = get_sg_grid_xy_points()
    xc, yc = (x_points[0] + x_points[-1]) / float(2), (y_points[0] + y_points[-1]) / float(2)
    color_map = ['red', 'green', 'blue', 'orange', 'black', 'purple', 'gray', 'white']
    #
    map_osm = folium.Map(location=[yc, xc], zoom_start=11)
    for x in x_points:
        sx, sy, ex, ey = x, y_points[0], x, y_points[-1]
        map_osm.add_children(folium.PolyLine(locations=[(sy, sx), (ey, ex)], weight=1.0))
    for y in y_points:
        sx, sy, ex, ey = x_points[0], y, x_points[-1], y
        map_osm.add_children(folium.PolyLine(locations=[(sy, sx), (ey, ex)], weight=1.0))
    #
    zones = get_sg_zones()
    zizj_tripNum_df = df.groupby(['zizj']).count()['did'].to_frame('numTrips').reset_index()
    for j, (zizj, _) in enumerate(zizj_tripNum_df.sort_values(by='numTrips', ascending=False).values):
        zi, zj = map(int, zizj.split('#'))
        y, x = zones[(zi, zj)].cCoor_gps
        folium.Marker((y, x),
                          popup='%d (%d#%d)' % (j, zi, zj),
                      icon=folium.Icon(color=color_map[0])
                      ).add_to(map_osm)
        if j == 10:
            break
    return map_osm

In [21]:
tm, year, gn = 'baseline', '2009', 'G(4)'
gt_dpath = dpaths[tm, year, 'groupTrips']
gt_prefix = prefixs[tm, year, 'groupTrips']
gt_fpath = '%s/%s%s.csv' % (gt_dpath, gt_prefix, gn)
df = pd.read_csv(gt_fpath)
#
map_osm = draw_interesting_zones_byNumVisit(df)
map_osm.save('/Users/JerryHan88/Desktop/baselineZones-G(4).html')
map_osm

In [26]:
tm, year, gn = 'baseline', '2009', 'G(4)'
gt_dpath = dpaths[tm, year, 'groupTrips']
gt_prefix = prefixs[tm, year, 'groupTrips']
gt_fpath = '%s/%s%s.csv' % (gt_dpath, gt_prefix, gn)
df = pd.read_csv(gt_fpath)
#
gz_dpath = dpaths[tm, year, 'groupZones']
gz_prefix = prefixs[tm, year, 'groupZones']
zizj_weight = load_pickle_file('%s/%s%s.pkl' % (gz_dpath, gz_prefix, gn))
#
map_osm = draw_interesting_zones(df, zizj_weight, True)
map_osm.save('/Users/JerryHan88/Desktop/collaborativeZones-%s.html' % gn)
map_osm

43#45 -131.70, 17, 1177
50#15 -99.60, 65, 1177
43#10 -171.15, 76, 1177
50#44 -82.72, 82, 1177
46#46 -98.90, 85, 1177
43#44 -89.60, 86, 1177
53#30 -50.76, 103, 1177
66#21 -74.32, 112, 1177
38#42 -121.40, 117, 1177
54#30 -46.00, 118, 1177
46#48 -69.84, 148, 1177
37#23 -189.12, 151, 1177
47#10 -130.24, 209, 1177
52#33 -38.53, 215, 1177
64#34 -144.33, 243, 1177
50#8 -123.93, 319, 1177
63#18 -103.19, 346, 1177
62#31 -109.15, 368, 1177
48#10 -58.55, 374, 1177
32#22 -22.63, 421, 1177
52#16 -203.79, 523, 1177
24#24 -41.36, 577, 1177
55#20 -41.48, 628, 1177
57#33 -79.97, 663, 1177
29#18 -28.75, 676, 1177
16#23 -89.70, 759, 1177


In [27]:
tm, year, gn = 'baseline', '2009', 'G(3)'
gt_dpath = dpaths[tm, year, 'groupTrips']
gt_prefix = prefixs[tm, year, 'groupTrips']
gt_fpath = '%s/%s%s.csv' % (gt_dpath, gt_prefix, gn)
df = pd.read_csv(gt_fpath)
#
gz_dpath = dpaths[tm, year, 'groupZones']
gz_prefix = prefixs[tm, year, 'groupZones']
zizj_weight = load_pickle_file('%s/%s%s.pkl' % (gz_dpath, gz_prefix, gn))
#
map_osm = draw_interesting_zones(df, zizj_weight, True)
map_osm.save('/Users/JerryHan88/Desktop/collaborativeZones-%s.html' % gn)
map_osm

85#27 -157.39, 0, 1290
85#26 -649.37, 1, 1290
53#16 -343.46, 7, 1290
51#14 -105.55, 9, 1290
54#14 -89.90, 14, 1290
55#13 -62.94, 16, 1290
55#16 -154.38, 17, 1290
54#10 -118.42, 18, 1290
53#14 -111.31, 41, 1290
36#30 -209.65, 46, 1290
23#24 -147.15, 72, 1290
51#12 -101.62, 74, 1290
54#19 -72.54, 77, 1290
52#7 -238.21, 81, 1290
44#11 -260.06, 84, 1290
32#31 -135.59, 122, 1290
40#37 -293.38, 141, 1290
27#24 -111.23, 149, 1290
61#31 -160.42, 163, 1290
46#9 -80.47, 193, 1290
30#22 -142.30, 195, 1290
51#23 -114.73, 204, 1290
44#10 -262.12, 211, 1290
48#18 -124.27, 214, 1290
26#24 -226.51, 243, 1290
59#20 -42.79, 258, 1290
32#24 -44.37, 267, 1290
51#44 -261.57, 270, 1290
24#24 -45.27, 275, 1290
36#32 -52.04, 280, 1290
48#13 -35.03, 285, 1290
45#7 -87.35, 288, 1290
55#17 -160.00, 291, 1290
71#20 -33.42, 330, 1290
62#33 -154.71, 355, 1290
48#8 -117.27, 371, 1290
39#13 -145.14, 389, 1290
72#25 -52.50, 440, 1290
42#45 -52.11, 580, 1290
46#20 -27.52, 589, 1290
46#46 -92.79, 613, 1290
53#31 -69.86,

In [25]:
tm, year, gn = 'baseline', '2009', 'G(3)'
gt_dpath = dpaths[tm, year, 'groupTrips']
gt_prefix = prefixs[tm, year, 'groupTrips']
gt_fpath = '%s/%s%s.csv' % (gt_dpath, gt_prefix, gn)
df = pd.read_csv(gt_fpath)
#
map_osm = draw_interesting_zones_byNumVisit(df)
map_osm.save('/Users/JerryHan88/Desktop/baselineZones-G(3).html')
map_osm